In [2]:
using Revise;
includet("../experiment/ringworld.jl")

┌ Info: Precompiling ActionRNNs [8317d1c6-c5c3-11e9-1282-0f8c4be94ea0]
└ @ Base loading.jl:1260


In [3]:
using Statistics, Plots, RollingFunctions, ActionRNNs, Flux
import Random

In [4]:
RWU = ActionRNNs.RingWorldUtils

ActionRNNs.RingWorldUtils

In [5]:
function construct_agent(outhorde, fc, rnn, opt, τ)


    # out_horde = RWU.gammas_term(collect(0.0:0.1:0.9))
#     out_horde = RWU.get_horde(parsed, "out")
    fs = MinimalRLCore.feature_size(fc)
#     fc, fs, chain = get_rnn_config(parsed, out_horde, rng)
    
#     opt_func = getproperty(Flux, Symbol(parsed["opt"]))
#     opt = opt_func(parsed["alpha"])

    
    ap = ActionRNNs.RandomActingPolicy([0.5, 0.5])

    ActionRNNs.FluxAgent(outhorde,
                         rnn,
                         opt,
                         τ,
                         fc,
                         fs,
                         ap)
end


construct_agent (generic function with 1 method)

In [10]:
fc = RWU.OneHotFeatureCreator()
fs = MinimalRLCore.feature_size(fc)
num_hidden = 12
outhorde = RWU.gammas_term([0.9])

Random.seed!(10392)

rnn = Chain(
    RNN(fs, num_hidden), 
#     Dense(num_hidden, num_hidden, relu),
    Dense(num_hidden, length(outhorde)))
opt = ADAM(0.0005)
τ = 8

agent = construct_agent(outhorde, fc, rnn, opt, τ)
env = RingWorld(6)

out_pred, out_err, out_loss = RingWorldExperiment.experiment_loop(env, agent, "gammas_term_one", 300000, Random.GLOBAL_RNG; prgs=true)

Step: 100%|█████████████████████████████████████████████| Time: 0:01:51


(Float32[-0.5982725 -0.20793727; -0.25284407 0.24242416; … ; 0.6019563 0.59420615; 1.0170649 0.65281326], Float32[-1.1297135 -0.7393783; -0.9089441 -0.75757587; … ; 0.070515305 0.06276515; 0.017064929 -0.0032867442], Float32[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0])

In [11]:
plot(rollmean(sqrt.(mean(out_err.^2; dims=2))[:,1], 1000))

In [12]:
out_pred - out_err

300000×2 Array{Float32,2}:
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 1.0       0.6561
 0.9       0.729
 1.0       0.6561
 0.9       0.729
 1.0       0.6561
 0.531441  0.531441
 0.6561    1.0
 0.729     0.9
 0.6561    1.0
 0.729     0.9
 ⋮         
 0.9       0.729
 0.81      0.81
 0.729     0.9
 0.6561    1.0
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 1.0       0.6561
 0.531441  0.531441
 0.6561    1.0
 0.531441  0.531441
 1.0       0.6561

In [13]:
out_pred

300000×2 Array{Float32,2}:
 -0.598273  -0.207937
 -0.252844   0.242424
 -0.81449   -0.316195
 -0.8078     0.898301
 -1.30521   -0.419656
 -1.36625    0.202145
 -1.16649    0.312682
 -1.26703    0.326543
 -0.625381  -0.524041
 -0.188647   0.678693
 -0.637576  -0.131937
 -0.657257   1.47897
 -1.25299    0.272554
  ⋮         
  0.912362   0.733261
  0.83178    0.816263
  0.746977   0.901017
  0.693539   1.0034
  0.600256   0.596947
  0.663529   1.02702
  0.603508   0.596245
  1.02246    0.657045
  0.604226   0.599076
  0.660731   1.02127
  0.601956   0.594206
  1.01706    0.652813